[爬蟲案例分享]
- 難點：

    1.資料量大，但每個查詢最多150個分頁，因此需要將查詢的範圍限縮。
    解決方式是在查詢時組合地區與職務類型，進行細緻的查詢。

    2.雖然幾乎沒有設定反爬蟲的機制，但每個 request 送的速度太快仍然會有失敗的狀況發生
    用while迴圈，當request成功是繼續前往下一頁爬蟲，request成功但資料小於20筆，查詢下一個組合，request等於20，表示還有資料需要繼續抓下一個分頁的資料。

    3.因為資料量大，建議按照組別存一次資料，這樣遇到錯誤時才不用重新爬資料。

    
- 因為查詢職缺最多有20\*150=3000筆資料，所以要將查詢的的條件透過條件進行篩選、排列組合，藉此撈出完整的資料
- 由公司資訊：地址，聯絡電話、職務
- 縣市和職務的分類有個資的代號，但中間有經過變(如縣市合併)更並不是單純的序列，因此要花時間找一下
- 可以看各個縣市的職缺數量與職務類型，進一步分析需要什麼技能
- 你要在哪裡，需要什麼技能、待遇如何
- 可以去串各縣市的人口數、教育程度等資訊
- 縣市的產業結構
- 可行的分析項目

# 載入套件

In [2]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import json
import re
import time
import os
import gc
from IPython.display import clear_output

In [1]:
headers={'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/84.0.4147.135 Safari/537.36',
         'Referer': 'https://www.104.com.tw/',
         'Host': 'www.104.com.tw',
         'DNT':'1',
         'Cookie':'GoogleBot'}

# 職缺清單
- 透過地區與職務分類來請求職缺資料

In [3]:
# 地區代碼
url = 'https://static.104.com.tw/category-tool/json/Area.json'
resp = requests.get(url)
df1 = []
for i in resp.json()[0]['n']:
    ndf = pd.DataFrame(i['n'])
    ndf['city'] = i['des']
    df1.append(ndf)
df1=pd.concat(df1, ignore_index=True)
df1 = df1.loc[:,['city','des','no']]
df1 = df1.sort_values('no')
df1.head()

city     des          no
0  台北市  台北市中正區  6001001001
1  台北市  台北市大同區  6001001002
2  台北市  台北市中山區  6001001003
3  台北市  台北市松山區  6001001004
4  台北市  台北市大安區  6001001005

In [4]:
url= 'https://static.104.com.tw/category-tool/json/JobCat.json'
resp = requests.get(url)
df2 = []
for i in resp.json():
    for j in i['n']:
        ndf = pd.DataFrame(j['n'])
        ndf.columns = ['des3','no3']
        ndf['des2'] = j['des']# 職務中分類
        ndf['no2'] = j['no']
        ndf['des1'] = i['des']# 職務大分類
        ndf['no1'] = i['no']
        df2.append(ndf)
df2 = pd.concat(df2, ignore_index=True)
df2 = df2.sort_values('no3')
print(df2.shape)
df2.head()

(466, 6)


des3         no3      des2         no2    des1         no1
1  經營管理主管  2001001001  經營╱幕僚類人員  2001001000  經營╱人資類  2001000000
0    儲備幹部  2001001002  經營╱幕僚類人員  2001001000  經營╱人資類  2001000000
2  主管特別助理  2001001003  經營╱幕僚類人員  2001001000  經營╱人資類  2001000000
3  人力資源主管  2001002001   人力資源類人員  2001002000  經營╱人資類  2001000000
6  人力資源人員  2001002002   人力資源類人員  2001002000  經營╱人資類  2001000000

In [5]:
# 捨棄最細的職務分類，減少重複爬相同職缺的情況
df2 = df2.drop_duplicates(['no2']).reset_index(drop=True)
print(df2.shape)
df2.head()

(44, 6)


des3         no3       des2         no2       des1         no1
0   經營管理主管  2001001001   經營╱幕僚類人員  2001001000     經營╱人資類  2001000000
1   人力資源主管  2001002001    人力資源類人員  2001002000     經營╱人資類  2001000000
2     行政主管  2002001001   行政╱總務類人員  2002001000  行政╱總務╱法務類  2002000000
3  法務╱智財主管  2002002001   法務╱智財類人員  2002002000  行政╱總務╱法務類  2002000000
4  財務或會計主管  2003001001  財務╱會計╱稅務類  2003001000   財會╱金融專業類  2003000000

In [6]:
# tmp = pd.DataFrame([re.sub('\.pkl','',file)for file in os.listdir('./data')],columns=['no'])
# df1 = pd.merge(df1, tmp, how='left',on='no',indicator=True)
# df1 = df1.loc[df1['_merge']!='both',:]
# df1

In [7]:
jobs = []
for areades, areacode in zip(df1['des'],df1['no']):
    for no2, des2 in zip(df2['no2'], df2['des2']):
        print(areades, ' | ', no2, ' - ', des2)
        page = 1
        while page <100:
            try:
                url = 'https://www.104.com.tw/jobs/search/list?ro=0&jobcat={}&jobcatExpansionType=1&area={}&order=11&asc=0&page={}&mode=l&jobsource=2018indexpoc'.format(no2, areacode, page)
                print(url)
                resp = requests.get(url, headers=headers)
                ndf = pd.DataFrame(resp.json()['data']['list'])
                print(ndf.shape)
                jobs.append(ndf)
                if ndf.shape[0]<30:
                    break
                else:
                    page += 1
            except:
                print('Retry')
        
jobs = pd.concat(jobs, ignore_index=True)
jobs.to_pickle('./data/data.pkl')
print('===================================  Save Data  ===================================')

台北市中正區  |  2001001000  -  經營╱幕僚類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(31, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=2&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=3&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=4&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=5&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=6&mode=l&jobsource=2018indexpoc
(3

(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2003001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=5&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2003001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=6&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2003001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=7&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2003001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=8&mode=l&jobsource=2018indexpoc
(20, 34)
台北市中正區  |  2003002000  -  金融專業相關類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2003002000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(32, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2003002000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=2&mode=l&jobsource=2018i

(16, 34)
台北市中正區  |  2004003000  -  專案╱產品管理類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2004003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(32, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2004003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=2&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2004003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=3&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2004003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=4&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2004003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=5&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2004003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=6&mode=l&jobsource=2018

(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2005002000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=34&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2005002000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=35&mode=l&jobsource=2018indexpoc
(17, 34)
台北市中正區  |  2005003000  -  業務銷售類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2005003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(38, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2005003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=2&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2005003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=3&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2005003000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=4&mode=l&jobsource=2018i

(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2006001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=14&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2006001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=15&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2006001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=16&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2006001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=17&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2006001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=18&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2006001000&jobcatExpansionType=1&area=6001001001&order=11&asc=0&page=19&mode=l&jobsource=2018indexpoc
(30, 34)
https://www.1

...

(0, 0)
金門縣烏坵鄉  |  2017002000  -  保全類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2017002000&jobcatExpansionType=1&area=6001022006&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
金門縣烏坵鄉  |  2018001000  -  農林漁牧相關類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2018001000&jobcatExpansionType=1&area=6001022006&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
金門縣烏坵鄉  |  2018002000  -  其他類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2018002000&jobcatExpansionType=1&area=6001022006&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣南竿鄉  |  2001001000  -  經營╱幕僚類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001001000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(7, 34)
連江縣南竿鄉  |  2001002000  -  人力資源類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2001002000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣南竿鄉  |  2002001000  

(0, 0)
連江縣南竿鄉  |  2016002000  -  教育輔導類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2016002000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(9, 34)
連江縣南竿鄉  |  2017001000  -  軍警消防類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2017001000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣南竿鄉  |  2017002000  -  保全類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2017002000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣南竿鄉  |  2018001000  -  農林漁牧相關類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2018001000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣南竿鄉  |  2018002000  -  其他類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2018002000&jobcatExpansionType=1&area=6001023001&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣北竿鄉  |  2001001000  -

(0, 0)
連江縣北竿鄉  |  2016001000  -  學術研究類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2016001000&jobcatExpansionType=1&area=6001023002&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣北竿鄉  |  2016002000  -  教育輔導類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2016002000&jobcatExpansionType=1&area=6001023002&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣北竿鄉  |  2017001000  -  軍警消防類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2017001000&jobcatExpansionType=1&area=6001023002&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣北竿鄉  |  2017002000  -  保全類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2017002000&jobcatExpansionType=1&area=6001023002&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣北竿鄉  |  2018001000  -  農林漁牧相關類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2018001000&jobcatExpansionType=1&area=6001023002&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣北竿鄉  |  2018002000  

(0, 0)
連江縣莒光鄉  |  2015001000  -  醫療專業類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2015001000&jobcatExpansionType=1&area=6001023003&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣莒光鄉  |  2015002000  -  醫療╱保健服務人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2015002000&jobcatExpansionType=1&area=6001023003&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
Retry
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2015002000&jobcatExpansionType=1&area=6001023003&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣莒光鄉  |  2016001000  -  學術研究類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2016001000&jobcatExpansionType=1&area=6001023003&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣莒光鄉  |  2016002000  -  教育輔導類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2016002000&jobcatExpansionType=1&area=6001023003&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(8, 34)
連江縣莒光鄉  |  2017001000  -  軍警消防類人員
https://www.104.com.t

(0, 0)
連江縣東引鄉  |  2014001000  -  文字編譯類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2014001000&jobcatExpansionType=1&area=6001023004&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣東引鄉  |  2014002000  -  記者及採訪類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2014002000&jobcatExpansionType=1&area=6001023004&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣東引鄉  |  2015001000  -  醫療專業類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2015001000&jobcatExpansionType=1&area=6001023004&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣東引鄉  |  2015002000  -  醫療╱保健服務人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2015002000&jobcatExpansionType=1&area=6001023004&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣東引鄉  |  2016001000  -  學術研究類人員
https://www.104.com.tw/jobs/search/list?ro=0&jobcat=2016001000&jobcatExpansionType=1&area=6001023004&order=11&asc=0&page=1&mode=l&jobsource=2018indexpoc
(0, 0)
連江縣東引鄉  |  201600200

In [9]:
jobs.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 446332 entries, 0 to 446331
Data columns (total 34 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   jobType         446332 non-null  object
 1   jobNo           446332 non-null  object
 2   jobName         446332 non-null  object
 3   jobNameSnippet  446332 non-null  object
 4   jobRole         446332 non-null  object
 5   jobRo           446332 non-null  object
 6   jobAddrNoDesc   446332 non-null  object
 7   jobAddress      446332 non-null  object
 8   description     446332 non-null  object
 9   optionEdu       446332 non-null  object
 10  period          446332 non-null  object
 11  periodDesc      446332 non-null  object
 12  applyCnt        446332 non-null  object
 13  applyDesc       446332 non-null  object
 14  custNo          446332 non-null  object
 15  custName        446332 non-null  object
 16  coIndustry      446332 non-null  object
 17  coIndustryDesc  446332 non-nu

# 職務內容
會擋IP，先用外層的資料分析，後續有時間再來處理代理IP和多線程的問題

In [3]:
jobs = pd.read_pickle('data/data.pkl')
print(jobs.shape)
jobs['link2'] = jobs['link'].apply(lambda x: 'https:'+x['job'].split(r'?')[0])
jobs = jobs.loc[:,['jobNo','link2']]
print(jobs.shape)
jobs = jobs.drop_duplicates('link2')
jobs = jobs.reset_index(drop=True)
print(jobs.shape)
jobs.head()

(446332, 34)
(446332, 2)
(268644, 2)


jobNo                             link2
0  10122438  https://www.104.com.tw/job/60yiu
1  11553567  https://www.104.com.tw/job/6vmsf
2  11826472  https://www.104.com.tw/job/71hd4
3   8119800  https://www.104.com.tw/job/4u1a0
4  11659955  https://www.104.com.tw/job/6xwvn

In [4]:
url = 'https://www.104.com.tw/job/ajax/content/7013z'
resp = requests.get(url,headers=headers)
data = resp.json()['data']
# header
# contact
# condition
# welfare
# jobDetail
# switch
# industry

In [5]:
data#['industry']

{'header': {'jobName': '金融菁英領航計劃(歡迎港、澳、外籍人才)', 'custName': '永豐金證券股份有限公司'},
 'switch': 'off',
 'custNo': '23113343000'}

In [6]:
', '.join(i['description'] for i in data['jobDetail']['jobCategory'])

KeyError: 'jobDetail'

In [ ]:
pd.DataFrame([{'jobName':data['header']['jobName'],
               'appearDate':data['header']['appearDate'],
               'custName':data['header']['custName'],
               'custUrl':data['header']['custUrl'],
               'hrName':data['contact']['hrName'],
               'email':data['contact']['email'],
               'phone':data['contact']['phone'],
               'other':data['contact']['other'],
               'acceptRole':', '.join(i['description'] for i in data['condition']['acceptRole']['role']), # 接受身份
               'workExp':data['condition']['workExp'],
               'edu':data['condition']['edu'], # 教育程度
               'major':', '.join(i for i in data['condition']['major']), # 科系要求
               'language':data['condition']['language'],
               'specialty':', '.join(i['description'] for i in data['condition']['specialty']), # 擅長工具
               'skill':', '.join(i['description'] for i in data['condition']['skill']), # 工作技能
               'other':data['condition']['other'], # 其他條件
               'welfare_tag':', '.join(i for i in data['welfare']['tag']), # 其他福利
               'welfare':data['welfare']['welfare'], # 福利制度
               'legalTag':data['welfare']['legalTag'], # 法定項目
               'jobDetail':data['jobDetail']['jobDescription'], # 工作內容
               'jobCategory': ', '.join(i['description'] for i in data['jobDetail']['jobCategory']),# 職務類別
               'salary':data['jobDetail']['salary'], # 工作待遇
               'salaryMin':data['jobDetail']['salaryMin'],
               'salaryMax':data['jobDetail']['salaryMax'],
               'salaryType':data['jobDetail']['salaryType'],
               'jobType':data['jobDetail']['jobType'],
               'workType':data['jobDetail']['workType'],
               'addressRegion':data['jobDetail']['addressRegion'],
               'addressDetail':data['jobDetail']['addressDetail'],
               'industryArea':data['jobDetail']['industryArea'],
               'longitude':data['jobDetail']['longitude'],
               'latitude':data['jobDetail']['latitude'],
               'manageResp':data['jobDetail']['manageResp'],
               'businessTrip':data['jobDetail']['businessTrip'],
               'workPeriod':data['jobDetail']['workPeriod'],
               'vacationPolicy':data['jobDetail']['vacationPolicy'],
               'startWorkingDay':data['jobDetail']['startWorkingDay'],
               'hireType':data['jobDetail']['hireType'],
               'delegatedRecruit':data['jobDetail']['delegatedRecruit'],
               'needEmp':data['jobDetail']['needEmp'],
               'switch':data['switch'],
               'industry':data['industry']
              }])

In [7]:
len(jobs['link2'])

268644

In [9]:
df = []
fail_cnt = 0
for num, code in enumerate(jobs['link2']):
    if num % 100 == 0:
        print(num)
    # 職缺內容
    url2 = 'https://www.104.com.tw/job/ajax/content/' + code.split(r'/')[-1]
    resp = requests.get(url2, headers=headers)
    # 會有些異常的職缺沒有資料，同 try 函數 parse 資料
    try:
        data = resp.json()['data']
        ndf = pd.DataFrame([{'jobName': data['header']['jobName'],
                             'appearDate':data['header']['appearDate'],
                             'custName':data['header']['custName'],
                             'custUrl':data['header']['custUrl'],
                             'hrName':data['contact']['hrName'],
                             'email':data['contact']['email'],
                             'phone':data['contact']['phone'],
                             'other':data['contact']['other'],
                             'acceptRole':', '.join(i['description'] for i in data['condition']['acceptRole']['role']), # 接受身份
                             'workExp':data['condition']['workExp'],
                             'edu':data['condition']['edu'],  # 教育程度
                             'major':', '.join(i for i in data['condition']['major']),# 科系要求
                             'language':data['condition']['language'],
                             'specialty':', '.join(i['description'] for i in data['condition']['specialty']),# 擅長工具
                             'skill':', '.join(i['description'] for i in data['condition']['skill']),# 工作技能
                             'other':data['condition']['other'],  # 其他條件
                             'welfare_tag':', '.join(i for i in data['welfare']['tag']),# 其他福利
                             'welfare':data['welfare']['welfare'],  # 福利制度
                             'legalTag':data['welfare']['legalTag'],  # 法定項目
                             'jobDetail':data['jobDetail']['jobDescription'],# 工作內容
                             'jobCategory': ', '.join(i['description'] for i in data['jobDetail']['jobCategory']),# 職務類別
                             'salary':data['jobDetail']['salary'],  # 工作待遇
                             'salaryMin':data['jobDetail']['salaryMin'],
                             'salaryMax':data['jobDetail']['salaryMax'],
                             'salaryType':data['jobDetail']['salaryType'],
                             'jobType':data['jobDetail']['jobType'],
                             'workType':data['jobDetail']['workType'],
                             'addressRegion':data['jobDetail']['addressRegion'],
                             'addressDetail':data['jobDetail']['addressDetail'],
                             'industryArea':data['jobDetail']['industryArea'],
                             'longitude':data['jobDetail']['longitude'],
                             'latitude':data['jobDetail']['latitude'],
                             'manageResp':data['jobDetail']['manageResp'],
                             'businessTrip':data['jobDetail']['businessTrip'],
                             'workPeriod':data['jobDetail']['workPeriod'],
                             'vacationPolicy':data['jobDetail']['vacationPolicy'],
                             'startWorkingDay':data['jobDetail']['startWorkingDay'],
                             'hireType':data['jobDetail']['hireType'],
                             'delegatedRecruit':data['jobDetail']['delegatedRecruit'],
                             'needEmp':data['jobDetail']['needEmp'],
                             'switch':data['switch'],
                             'industry':data['industry']
                             }])
        df.append(ndf)
    except:
        fail_cnt += 1
        print(url2)
df = pd.concat(df, ignore_index=True)
df

0
https://www.104.com.tw/job/ajax/content/7013z
https://www.104.com.tw/job/ajax/content/6ypm2
https://www.104.com.tw/job/ajax/content/4jwyj
https://www.104.com.tw/job/ajax/content/4js2e
https://www.104.com.tw/job/ajax/content/4dnfp
https://www.104.com.tw/job/ajax/content/71yn5
100
200
300
400
https://www.104.com.tw/job/ajax/content/71c64
https://www.104.com.tw/job/ajax/content/5osyj
500
https://www.104.com.tw/job/ajax/content/5vnvk


ConnectionError: ('Connection aborted.', OSError("(10054, 'WSAECONNRESET')"))

In [10]:
df = []
for i in os.listdir('./data/'):
    ndf = pd.read_pickle('./data/' + i)
    df.append(ndf)
df = pd.concat(df, ignore_index=True)
df

公司名稱             公司編號        公司類別        公司類別描述  \
0         德信綜合證券股份有限公司      23470432000  1004002002        證券及期貨業   
1           聯邦保全股份有限公司      70691148000  1009006001       保全樓管相關業   
2               恬媞琳美容坊      13849529000  1009005002        美容／美體業   
3            財團法人信誼基金會      82003814000  1013002002          職業團體   
4          財團法人綠色和平基金會      26324671000  1013001003     國際組織及外國機構   
...                ...              ...         ...           ...   
551659        佑呈開發有限公司  130000000136697  1012002001  環境衛生及污染防治服務業   
551660        佑呈開發有限公司  130000000136697  1012002001  環境衛生及污染防治服務業   
551661  財團法人中華民國唐氏症基金會      81598577000  1013003001       社會福利服務業   
551662  財團法人中華民國唐氏症基金會      81598577000  1013003001       社會福利服務業   
551663  財團法人中華民國唐氏症基金會      81598577000  1013003001       社會福利服務業   

                                                     公司連結  \
0       //www.104.com.tw/company/as5ot8g?jobsource=201...   
1       //www.104.com.tw/company/wh3omw0?jobsource=201...   
2       //www.104.com.tw/company/6d1ngyw?jobsource=201...   
3       //www.104.com.tw/company/11o6ybu8?jobsource=20...   
4       //www.104.com.tw/company/c3d1254?jobsource=201...   
...                                                   ...   
551659  //www.104.com.tw/company/1a2x6bkws9?jobsource=...   
551660  //www.104.com.tw/company/1a2x6bkws9?jobsource=...   
551661  //www.104.com.tw/company/11hhooyw?jobsource=20...   
551662  //www.104.com.tw/company/11hhooyw?jobsource=20...   
551663  //www.104.com.tw/company/11hhooyw?jobsource=20...   

                              職缺名稱 職務性質        職缺大分類       職缺中分類  \
0                           董事長室特助    1       經營╱人資類    經營╱幕僚類人員   
1                           綜管勤務幹部    1       經營╱人資類    經營╱幕僚類人員   
2                        門市店長(台大店)    1       經營╱人資類    經營╱幕僚類人員   
3                              數位長    1       經營╱人資類    經營╱幕僚類人員   
4       Action Unit Manager 行動統籌經理    1       經營╱人資類    經營╱幕僚類人員   
...                            ...  ...          ...         ...   
551659          【環保工程】約聘專案工程師（連江縣）    1  行銷╱企劃╱專案管理類  專案╱產品管理類人員   
551660          【環保工程】約聘專案工程師（連江縣）    1  生產製造╱品管╱環衛類   環境安全衛生類人員   
551661         托育人員(連江縣西莒社區公共托育家園)    1    學術╱教育╱輔導類     教育輔導類人員   
551662         托育人員(連江縣東莒社區公共托育家園)    1    學術╱教育╱輔導類     教育輔導類人員   
551663           托育人員(連江縣東引公共托育中心)    1    學術╱教育╱輔導類     教育輔導類人員   

               職缺小分類      職缺編號  \
0             經營管理主管  11085193   
1             經營管理主管  11303945   
2             經營管理主管   8368962   
3             經營管理主管  10622980   
4             經營管理主管  11673371   
...              ...       ...   
551659       其他專案管理師  11616392   
551660  環境工程人員 / 工程師  11616392   
551661           教保員  11544859   
551662           教保員  11544841   
551663           教保員   8919271   

                                                     職務內容  更新日期  \
0                    1.提供董事長經營管理建議及執行\r\n2.協助處理法律相關案件\r\n  6/18   
1       1. 保全人員班表排定製作(每月底前)\r\n2. 保全勤務調度(臨時或緊急狀況排除)\r\...  6/18   
2       1.美容店務管理。\r\n2.人員在職訓練管理。\r\n3.客戶售後服務之規劃安排\r\n4...  6/18   
3       1. 整合組織資源，帶領組織數位轉型。\r\n2. 資料庫與跨平台服務之建構.營運及推廣。\r\n  6/17   
4       We are HIRING!!!\r\n\r\nGreenpeace is a non-pr...  6/17   
...                                                   ...   ...   
551659  協助公司連江縣北竿鄉專案計畫執行與管理,包含: \r\n1、環保專案計畫執行溝通協調 \r\...  6/08   
551660  協助公司連江縣北竿鄉專案計畫執行與管理,包含: \r\n1、環保專案計畫執行溝通協調 \r\...  6/08   
551661                                    嬰幼兒照護與保育工作(供住宿)  6/15   
551662                                    嬰幼兒照護與保育工作(供住宿)  6/15   
551663                                         嬰幼兒照護與保育工作  6/15   

                                                     職缺連結  \
0       //www.104.com.tw/job/6lle1?jobsource=2018indexpoc   
1       //www.104.com.tw/job/6qa6h?jobsource=2018indexpoc   
2       //www.104.com.tw/job/4zdj6?jobsource=2018indexpoc   
3       //www.104.com.tw/job/6boqs?jobsource=2018indexpoc   
4       //www.104.com.tw/job/6y78b?jobsource=2018indexpoc   
...                                                   ...  

In [12]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 551664 entries, 0 to 551663
Data columns (total 19 columns):
 #   Column  Non-Null Count   Dtype 
---  ------  --------------   ----- 
 0   公司名稱    551664 non-null  object
 1   公司編號    551664 non-null  object
 2   公司類別    551664 non-null  object
 3   公司類別描述  551664 non-null  object
 4   公司連結    551664 non-null  object
 5   職缺名稱    551664 non-null  object
 6   職務性質    551664 non-null  object
 7   職缺大分類   551664 non-null  object
 8   職缺中分類   551664 non-null  object
 9   職缺小分類   551664 non-null  object
 10  職缺編號    551664 non-null  object
 11  職務內容    551664 non-null  object
 12  更新日期    551664 non-null  object
 13  職缺連結    551664 non-null  object
 14  標籤      551664 non-null  object
 15  公司地址    551664 non-null  object
 16  地區      551664 non-null  object
 17  經歷      551664 non-null  object
 18  學歷      551664 non-null  object
dtypes: object(19)
memory usage: 80.0+ MB


In [11]:
df.to_excel('./JobList.xlsx')